In [1]:
import gensim
import numpy as np
import pandas as pd
import re
import string
import nltk
#nltk.download('punkt')

data = pd.read_csv('newmeta.csv', low_memory= False)

#Remove punctuation and lower case all characters
def clean(txt):
    txt = re.sub("[^a-zA-Z ]", "", str(txt))
    txt = txt.lower()
    txt = nltk.word_tokenize(txt)
    return txt

token_data = data['abstract'].apply(clean)

#Using gensim to generate model below
#I'm unsure of whether using the token_data as the corpus
#is the most efficient approach without any windowing or size
model = gensim.models.Word2Vec(token_data, size = 100)

#Save for future use
model.save("w2v.model")

#Below section is just to test that we've read in correctly
five_word = [x for x in model.wv.vocab][0:5]
print(five_word)

['objective', 'this', 'retrospective', 'chart', 'review']


In [7]:
pip install plotly

     |████████████████████████████████| 11.5 MB 11.9 MB/s eta 0:00:01
  Created wheel for retrying: filename=retrying-1.3.3-py3-none-any.whl size=11430 sha256=f0af45b8b77edbc52fa59502a1a89641fa092be6e47cb3d048c64bbf4e28ad89
  Stored in directory: /Users/keaton/Library/Caches/pip/wheels/f9/8d/8d/f6af3f7f9eea3553bc2fe6d53e4b287dad18b06a861ac56ddf
Successfully built retrying
Note: you may need to restart the kernel to use updated packages.


In [6]:
pip install sklearn

SyntaxError: invalid syntax (<ipython-input-6-26f3d21206fc>, line 1)

In [8]:
import plotly
from sklearn.decomposition import IncrementalPCA    # inital reduction
from sklearn.manifold import TSNE                   # final reduction
import numpy as np                                  # array handling


def reduce_dimensions(model):
    num_dimensions = 2  # final num dimensions (2D, 3D, etc)

    vectors = [] # positions in vector space
    labels = [] # keep track of words to label our data again later
    for word in model.wv.vocab:
        vectors.append(model.wv[word])
        labels.append(word)

    # convert both lists into numpy vectors for reduction
    vectors = np.asarray(vectors)
    labels = np.asarray(labels)

    # reduce using t-SNE
    vectors = np.asarray(vectors)
    tsne = TSNE(n_components=num_dimensions, random_state=0)
    vectors = tsne.fit_transform(vectors)

    x_vals = [v[0] for v in vectors]
    y_vals = [v[1] for v in vectors]
    return x_vals, y_vals, labels


x_vals, y_vals, labels = reduce_dimensions(model)

def plot_with_plotly(x_vals, y_vals, labels, plot_in_notebook=True):
    from plotly.offline import init_notebook_mode, iplot, plot
    import plotly.graph_objs as go

    trace = go.Scatter(x=x_vals, y=y_vals, mode='text', text=labels)
    data = [trace]

    if plot_in_notebook:
        init_notebook_mode(connected=True)
        iplot(data, filename='word-embedding-plot')
    else:
        plot(data, filename='word-embedding-plot.html')


def plot_with_matplotlib(x_vals, y_vals, labels):
    import matplotlib.pyplot as plt
    import random

    random.seed(0)

    plt.figure(figsize=(12, 12))
    plt.scatter(x_vals, y_vals)

    #
    # Label randomly subsampled 25 data points
    #
    indices = list(range(len(labels)))
    selected_indices = random.sample(indices, 25)
    for i in selected_indices:
        plt.annotate(labels[i], (x_vals[i], y_vals[i]))

try:
    get_ipython()
except Exception:
    plot_function = plot_with_matplotlib
else:
    plot_function = plot_with_plotly

plot_function(x_vals, y_vals, labels)